# Writen By Zhang Shaobin ...

In [4]:
import re
import os
import json
import unicodedata
import numpy as np
import pandas as pd

## Traditional Raw CSV Files

load the trd raw file

In [5]:
trd_file_path = "/Users/shaobin/Personal/In Hong Kong/Semester-B/Project/data/Medical_Insurance_Data_Collection/pdfFiles/trd_raw.csv"
df = pd.read_csv(trd_file_path)
json_files = json.loads(df.to_json(orient = 'records'))

In [7]:
print(json_files[0])
print(json_files[1])

{'product_id': 0, 'ref_page': 1, 'brochure_text': '智適簡自願醫療保險計劃\n保單條文\n目錄\n第一部分 保險條文及保單 .................................................................................................................................... 2\n第二部分 一般條件 ............................................................................................................................................... 4\n第三部分 保費條文 .............................................................................................................................................10\n第四部分 續保條文 .............................................................................................................................................11\n第五部分 索償條文 .............................................................................................................................................14\n第六部分 保障條文 .............................................................................................................................................15\n

### Remove Page Number

In [8]:
pattern = r'\d+$|第\d+頁'
for i in range(len(json_files)):
    texts = json_files[i]['brochure_text']
    match = re.search(pattern, texts)
    if match:
        json_files[i]['brochure_text'] = texts[:match.start()]
json_files

[{'product_id': 0,
  'ref_page': 1,
  'brochure_text': '智適簡自願醫療保險計劃\n保單條文\n目錄\n第一部分 保險條文及保單 .................................................................................................................................... 2\n第二部分 一般條件 ............................................................................................................................................... 4\n第三部分 保費條文 .............................................................................................................................................10\n第四部分 續保條文 .............................................................................................................................................11\n第五部分 索償條文 .............................................................................................................................................14\n第六部分 保障條文 ............................................................................................................................................

### Normalized the Unicode of String

In [9]:
for json_file in json_files:
    json_file['brochure_text'] = unicodedata.normalize('NFKC', json_file['brochure_text'])
json_files

[{'product_id': 0,
  'ref_page': 1,
  'brochure_text': '智適簡自願醫療保險計劃\n保單條文\n目錄\n第一部分 保險條文及保單 .................................................................................................................................... 2\n第二部分 一般條件 ............................................................................................................................................... 4\n第三部分 保費條文 .............................................................................................................................................10\n第四部分 續保條文 .............................................................................................................................................11\n第五部分 索償條文 .............................................................................................................................................14\n第六部分 保障條文 ............................................................................................................................................

### Section Breakdown

In [10]:
def section_break(df_text, sections):
    i, json_row = 0, {}
    
    if df_text.count('第一部分 保險條文及保單') > 1:
        end = df_text.find('第一部分 保險條文及保單') + len(sections[i])
    else:
        end = 0
        
    while i < len(sections):
        if sections[i] in df_text:
            start = df_text.find(sections[i], end) + len(sections[i])
            if i == 0: 
                json_row["前綴信息"] = df_text[ :start - len(sections[0])]
            if i == len(sections) - 1:
                json_row[sections[i]] = df_text[start: ]
                break
            j = i + 1
            while j < len(sections):
                if sections[j] in df_text:
                    end = df_text.find(sections[j], start)
                    json_row[sections[i]] = df_text[start:end]
                    break
                elif j == len(sections) - 1:
                    json_row[sections[i]] = df_text[start: ]
                j += 1
        i += 1
    
    return json_row

In [11]:
df_json = []
sections = ['第一部分 保險條文及保單', '第二部分 一般條件', '第三部分 保費條文', '第四部分 續保條文', '第五部分 索償條文', 
            '第六部分 保障條文', '第七部分 一般不保事項', '第八部分 釋義', '第九部分 多名保單持有人條文']

for i in range(json_files[-1]['product_id'] + 1):
    json_file = [item for item in json_files if item['product_id'] == i]
    df_text = ''.join([item['brochure_text'] for item in json_file])
    json_row = section_break(df_text, sections)
    json_row['product_id'] = i
    df_json.append(json_row)

df_json

[{'前綴信息': '智適簡自願醫療保險計劃\n保單條文\n目錄\n第一部分 保險條文及保單 .................................................................................................................................... 2\n第二部分 一般條件 ............................................................................................................................................... 4\n第三部分 保費條文 .............................................................................................................................................10\n第四部分 續保條文 .............................................................................................................................................11\n第五部分 索償條文 .............................................................................................................................................14\n第六部分 保障條文 .............................................................................................................................................15\n第七部分 一般不保事項.............................

In [12]:
with open("section_break_json", "w", encoding="utf-8") as file:
    json.dump(df_json, file, ensure_ascii=False)

In [13]:
with open("section_break_json", "r", encoding="utf-8") as file:
    df_json = json.load(file)
    print(df_json[0]['第八部分 釋義'])


本條款及保障中使用的字詞及表述必須按照以下所述解釋 –
「意外」 是指因暴力、外在及可見因素引致的突發事故,並且完全非受保人所能預見及控
制。
「年齡」 是指受保人的實際年齡。
「每年保障限額」 是指本公司在每個保單年度內向保單持有人支付的最高賠償限額,不論任何在保
障表中所列的保障項目是否已經達到其相關項目的賠償限額。
每年保障限額在每個新保單年度會重新計算。
「投保申請文件」 是指向本公司就本認可産品遞交的投保申請,包括與該投保申請有關的投保申請
表格、問卷、可保性的證明、任何已提交的文件或資料,以及已作出的陳述及聲
明(若本公司在第一部分第8節提出要求,則包括相關必需資料的任何更新及改
動)。
「保障表」 是指本條款及保障所附的保障表,當中必須列明所涵蓋的保障項目及最高賠償限
額。
「個別不保項目」 是指本公司可按受保人的投保前已有病症或其他影響其可保性的因素,就特定的
不適或疾病而加設的不保承項目,訂明在本條款及保障中不保障。
「認可產品」 是指經政府認可為符合自願醫保内相關合規要求的保險産品内所有條款及保障(包
括任何補充文件) 。本認可產品內容包括本條款及細則和保障表及以下補充文件 –
(a) 補充文件 - 增值稅和商品及服務稅納入為合資格費用
(b) 補充文件 - 香港公營醫院及私營醫院納入醫院的釋義
「共同保險」 是指保單持有人在支付毎個保單年度的自付費後(如有),必須按比率分擔的合資
格費用。為免存疑,共同保險並非指在實際費用超出本條款及保障賠償限額的情
況下,保單持有人需支付的任何差額。
「本公司」 是指保特保險(香港)有限公司。
「住院」 是指受保人在醫療所需的情況下,按註冊醫生的建議以住院病人身份入住醫院以
接受醫療服務。
住院必須以醫院開出的每日病房費單據作證明,受保人必須在整個住院期間連續
留院。
「先天性疾病」 是指 (a) 任何於出生時或之前已存在的醫學、生理或精神上的異常,不論於出生
時有關異常是否已出現、被確診或獲知悉;或 (b) 任何於出生後六 (6) 個月內出
現的新生嬰兒異常。
本頁內容屬於自願醫保認可產品(編號: S00012)的條款及保障。
「日間手術」 是指受保人作為日症病人在具備康復設施的診所、日間手術中心或醫院內因檢查
或治療而進行醫療所需的外科手術。
「日症病人」 是指在診所、日間手術中心或醫院(非住院性質)接

In [18]:
with open("section_break_json", "r", encoding="utf-8") as file:
    df_json = json.load(file)
    for j in range(32):
        print("proudct_id: ", j)
        for key in df_json[j].keys():
            print(key)
            if(type(df_json[j][key]) != str):
                break
            print(len(df_json[j][key]))


proudct_id:  0
前綴信息
1428
第一部分 保險條文及保單
1680
第二部分 一般條件
5760
第三部分 保費條文
435
第四部分 續保條文
2738
第五部分 索償條文
764
第六部分 保障條文
3702
第七部分 一般不保事項
1710
第八部分 釋義
5253
第九部分 多名保單持有人條文
12908
product_id
proudct_id:  1
前綴信息
2097
第一部分 保險條文及保單
1778
第二部分 一般條件
6124
第三部分 保費條文
501
第四部分 續保條文
2124
第五部分 索償條文
833
第六部分 保障條文
4103
第七部分 一般不保事項
1865
第八部分 釋義
18320
product_id
proudct_id:  2
前綴信息
1347
第一部分 保險條文及保單
1687
第二部分 一般條件
5814
第三部分 保費條文
435
第四部分 續保條文
1984
第五部分 索償條文
762
第六部分 保障條文
3747
第七部分 一般不保事項
1716
第八部分 釋義
17482
product_id
proudct_id:  3
前綴信息
1125
第一部分 保險條文及保單
1734
第二部分 一般條件
5928
第三部分 保費條文
465
第四部分 續保條文
2827
第五部分 索償條文
796
第六部分 保障條文
3888
第七部分 一般不保事項
1769
第八部分 釋義
17249
product_id
proudct_id:  4
前綴信息
643
第一部分 保險條文及保單
1711
第二部分 一般條件
5927
第三部分 保費條文
439
第四部分 續保條文
2785
第五部分 索償條文
779
第六部分 保障條文
3767
第七部分 一般不保事項
1724
第八部分 釋義
18691
product_id
proudct_id:  5
前綴信息
1384
第一部分 保險條文及保單
1740
第二部分 一般條件
6078
第三部分 保費條文
443
第四部分 續保條文
2446
第五部分 索償條文
817
第六部分 保障條文
3865
第七部分 一般不保事項
1771
第八部分 釋義
16149
product_id
proudct_id:  6
前綴信息
1050
第一部分 保險條